In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
from setupFigure import SetupFigure
from dftSlow import dft_coeff, dft_synthesis

In [ ]:
def dft_fast_coeff(x):
    """
    Evaluate Fourier coefficients using Numpy's fast Fourier transform.
    This routine only returns the coefficients for the positive frequencies.
    If N is even, it goes up to n=N/2.
    If N is odd, it goes up to n=(N-1)/2.
    :param x: array of function samples
    """
    return np.fft.rfft(x, norm='forward')

In [ ]:
def dft_fast_synthesis(fc, outnum='even'):
    """
    Use numpy's fast Fourier synthesis taking only Fourier coefficients for positive frequencies
    :param fc: aray of coefficients for positive frequencies only.
    :param outnum: specifies if output time series has an even or odd number of samples (default: 'even')
    """
    ns = 2*fc.size-2
    if outnum == 'odd': ns = 2*fc.size-1
    return np.fft.irfft(fc, ns, norm='forward')

In [ ]:
def boxcar(dt, period, tup, tdown):
    """
    Calculate samples of a boxcar function
    :param dt: sampling interval
    :param period: time range is 0 <= t < period (multiple of dt)
    :param tup: time where boxcar goes from 0 to 1
    :param tdown: time where boxcar goes from 1 to 0
    """
    ns = int(period/dt)
    t = dt*np.arange(0, ns)
    return t, np.where(t < tup, 0, 1)*np.where(t > tdown, 0, 1)

In [ ]:
def gaussian(dt, period, tmax, hwidth):
    """
    Calculate samples of a Gaussian function
    :param dt: sampling interval
    :param period: time range is 0 <= t < period (multiple of dt)
    :param tmax: time of maximum of Gaussian
    :param hwidth: half width of Gaussian
    """
    ns = int(period/dt)
    t = dt*np.arange(0, ns)
    return t, np.exp(-(t-tmax)**2/hwidth**2)

## Task 1: Compare "slow" Fourier transform with the fast version of numpy

Again set up the boxcar function as in the previous assignment and use the provided functions to compute the Fourier coefficients by both methods. Verify that both methods yield the same results by printing the first 20 coefficients.

In [ ]:
t, bx = boxcar(1, 1000, 300, 500)

In [ ]:
c = dft_coeff(bx)                  # slow DFT
fc = dft_fast_coeff(bx)            # fast DFT
print(t.size, c.size, fc.size)
for n in range(t.size//50):
    print("{:6d}    {:15.6e}   {:15.6e}".format(n, c[n], fc[n]))

Also compare the slow and fast versions of Fourier synthesis by calling the provided functions. Print values at times around the discontinuities.

In [ ]:
xr = dft_synthesis(c)
if t.size%2 == 0:
    xrf = dft_fast_synthesis(fc, outnum='even')
else:
    xrf = dft_fast_synthesis(fc, outnum='odd')
print(xr.size, xrf.size)
for k in range(290,311):
    print("{:6d} {:15.6e} {:15.6e}".format(k, xr[k], xrf[k]))

## Task 2: Interpolation by appending zeros to the Fourier coefficients

A band limited time series can be interpolated using a simple trick: First, the Fourier coefficients are computed up to the Nyquist frequency, $f_{Ny} = \frac{N}{2}\Delta f = \frac{N}{2T}$. Then, $L$ zero coefficents are appended to increase the Nyquist frequency to $f'_{Ny} = (\frac{N}{2}+L)\Delta f$ and to decrease the sampling interval to $\Delta t' = \frac{1}{2f'_{Ny}}$. Subsequent Fourier synthesis produces an interpolated version of the original time series. These relations hold for even and odd number of samples.
When doing the Fourier synthesis, the routine should be called with outnum='odd' for odd N and with outnum='even' for even N, respectively.

First set up a Gaussian using the provided function. Then compute the Fourier coefficients. Print out the number of samples, the Nyquist frequency and the number of Fourier coefficients. For example, choose dt=5, period=100, tmax=50, hw=20. 

Second, append some zeros (20) to the array of coefficients and compute the new Nyquist frequency and the new sampling interval. Do the Fourier synthesis and print the new number of samples, the new Nyquist frequency and the new sampling interval.

Third, plot the new and old time series into one graph.

In [ ]:
dt = 5; period = 100; tmax = 50; hw = 20; nz = 20
t, g = gaussian(dt, period, tmax, hw)
c = dft_fast_coeff(g)
print("N = ", t.size," Nyquist frequency = ", t.size/(2*period)," Ncoeff = ", c.size)

In [ ]:
cz = np.append(c, np.zeros(nz))
fny = (t.size/2+nz)/period
dtnew = 1./(2*fny)
if t.size%2 != 0:
    xr = dft_fast_synthesis(cz, outnum='odd')
else:
    xr = dft_fast_synthesis(cz, outnum='even')
tz = dtnew*np.arange(0, xr.size)
print("N = ", tz.size," Nyquist frequency = ", fny)

In [ ]:
fig1, ax1 = SetupFigure(10, 5, "Time [s]", "xr(t)", "Interpolated Gaussian", 14)
ax1.plot(tz, xr, color='blue', ls='-', lw=0.25, marker='d', markersize=4, zorder=10)
ax1.plot(t, g, color='red', ls='', marker='o', markersize=6, zorder=5)

## Task 3: Aliasing and the sampling theorem

First, calculate values for a Gaussian with dt=0.25, period=100, tmax=50 and hwidth=1. Plot the Gaussian.

Second, in a loop, calculate sme Gaussian with dt = 0.5, 1.0, 1.5 and 2.0. Compute the fast Fourier coefficients and the frequencies associated with them. Plot the absolute value of the coefficients into one graph. Set the upper frequency axis limit to 1.0 and use different colors for the curves. Compare the spectra, what do you observe?

In [ ]:
t, g = gaussian(0.25, 100, 50, 1)
fig3, ax3 = SetupFigure(10, 3, "Time [s]", "g(t)", "Sharp Gaussian", 14)
ax3.plot(t, g, color='blue', ls='-', lw=1.0)

In [ ]:
fig2, ax2 = SetupFigure(10, 5, "Frequency [s]", "G(f)", "Fourier coefficients", 14)
ax2.set_xlim(0, 1.0)
col = ['grey', 'orange', 'red', 'magenta', 'blue']
lw = [4, 1, 1, 1, 1]
for i, dt in enumerate([0.25, 0.5, 1.0, 1.5, 2.0]):
    t, g = gaussian(dt, 100, 50, 1)
    c = dft_fast_coeff(g)
    f = 1./period*np.arange(0, c.size)
    ax2.plot(f, np.absolute(c), color=col[i], ls='-', lw=lw[i], label="DT = {:5.2f}".format(dt))
ax2.legend()    